# **SMM Assignment2**

在這份作業中，我們會使用Pytorch Geometric(PyG)來建構GCN模型，並將其應用到兩個OGB（Open Graph Benchmark）公開資料集上。一個資料集的任務是Node分類，另一個是圖分類。

首先，我們需要Pytorch Geometric將Graph資料存儲為Pytorch Tensor。

***請勿參考網路上的相關實作，也不能copy同學的code。**但你可以與同學或TA討論你遇到的問題。

In this assignment, we will use Pytorch Geometric (PyG) to construct the GCN model and apply it to two OGB (Open Graph Benchmark) public datasets. One dataset will be tasked with Node classification and the other with graph classification.

First, we need the Pytorch Geometric to store the Graph data as a Pytorch Tensor.

*Please do not refer to the related work on the web. But You can discuss your problems with your classmates or TA.


# 設備 Device

如果你使用Colab，請調整至GPU模式。

If you are using Colab, please adjust to GPU mode

# 安裝 Installation

In [1]:
!pip install -q torch==1.13.1+cu117 torchvision==0.14.1+cu117 torchaudio==0.13.1 torchdata torchtext --extra-index-url https://download.pytorch.org/whl/cu117
import torch
import os
print("PyTorch has version {}".format(torch.__version__))

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 GB 456.6 kB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.3/24.3 MB 57.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.2/4.2 MB 91.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.7/4.7 MB 85.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.6/4.6 MB 99.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.6/4.6 MB 109.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.6/4.6 MB 18.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 63.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 56.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 71.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 55.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 64.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.

In [2]:
# 確保下載的CUDA版本與上面一致
# please make sure the CUDA version's consistency
!pip install -q ogb
!pip install -q torch-geometric
!pip install -q --no-index torch-scatter -f https://pytorch-geometric.com/whl/torch-1.13.1+cu117.html
!pip install -q --no-index torch-sparse -f https://pytorch-geometric.com/whl/torch-1.13.1+cu117.html

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.8/78.8 kB 1.1 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 6.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.1/10.1 MB 18.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.7/4.7 MB 12.6 MB/s eta 0:00:00


# 1 PyTorch Geometric (Datasets and Data)


PyTorch Geometric有兩種用於存儲、轉換Graph至Tensor的Class。一個是`torch_geometric.datasets`，包括了一些常見的Graph資料集，另一個是`torch_geometric.data`，提供了資料轉換、數據處理的一些基本功能。

後續步驟中，建議你多閱讀官方文檔：https://pytorch-geometric.readthedocs.io/en/latest/

PyTorch Geometric has two classes for storing and converting Graphs to Tensor: `torch_geometric.datasets`, which includes some common Graph datasets, and `torch_geometric.data`, which provides basic functions for data conversion, data The other is `torch_geometric.data`, which provides some basic functions for data conversion, data processing, and so on.

For further steps, we recommend that you read the official documentation: https://pytorch-geometric.readthedocs.io/en/latest/

## PyG Datasets

`torch_geometric.datasets`提供常用資料集的下載，這邊我們以ENZYMES資料集為例。

`torch_geometric.datasets` provides commonly used datasets, here we take the ENZYMES dataset as an example.

In [3]:
from torch_geometric.datasets import TUDataset

root = './enzymes'
name = 'ENZYMES'

# The ENZYMES dataset
pyg_dataset= TUDataset('./enzymes', 'ENZYMES')

# You can find that there are 600 graphs in this dataset
print(pyg_dataset)

Processing...


ENZYMES(600)


Done!


## 第一題：ENZYMES中的Classes和Node的特徵數量為多少？（5分）

## Question 1: What is the number of Classes and features of Nodes in ENZYMES? (5 marks)

Please refer to: [here](https://pytorch-geometric.readthedocs.io/en/latest/modules/data.html)

In [4]:
def get_num_classes(pyg_dataset):

  num_classes = 0

  ############# CODE HERE ############
  ## 1. 可查詢InMemoryDataset的methods
  ## You can check the methods of the InMemoryDataset
  ## 2. 可參考自動補全給出的建議
  ## Check the advice given in the auto-completion
  num_classes = pyg_dataset.num_classes
  #########################################

  return num_classes

def get_num_features(pyg_dataset):
  # return the number of features for that dataset.

  num_features = 0

  ############# CODE HERE ############
  ## 建議同上
  ## Suggestions as above
  num_features = pyg_dataset.num_features
  #########################################

  return num_features

num_classes = get_num_classes(pyg_dataset)
num_features = get_num_features(pyg_dataset)
print("{} dataset has {} classes".format(name, num_classes))
print("{} dataset has {} features".format(name, num_features))

ENZYMES dataset has 6 classes
ENZYMES dataset has 3 features


## PyG Data

每個PyG Dataset通常存儲多個`torch_geometric.data.Data`物件。每個`torch_geometric.data.Data`物件都代表一張Graph。你可以透過索引的方式從Dataset取出`Data`。

關於`Data`物件的詳細說明，請閱讀[這裡](https://pytorch-geometric.readthedocs.io/en/latest/modules/data.html#torch_geometric.data.Data).

Each PyG Dataset usually stores multiple `torch_geometric.data.Data` objects. Each `torch_geometric.data.Data` object represents a Graph, and you can retrieve `Data` by indexing Dataset.

For a detailed description of the `Data` objects, please read [here](https://pytorch-geometric.readthedocs.io/en/latest/modules/data.html#torch_geometric.data.Data).

## 第二題：請問ENZYMES dataset中index為100的圖的label是什麼？（5分）
## Question 2： What is the label of the graph with index 100 in the ENZYMES dataset? (5 marks)

In [12]:
def get_graph_class(pyg_dataset, idx):
  # 輸入為PyG dataset物件和Index，輸出為該Graph的Label/Class（整型）。
  # Input is the PyG dataset object and Index, output is the Label/Class (integer) of the Graph.

  label = -1

  ############# CODE HERE ############
  label = pyg_dataset.get(idx).y
  #########################################

  return label

graph_0 = pyg_dataset[0]
print(graph_0)
idx = 100
label = get_graph_class(pyg_dataset, idx)
print('Graph with index {} has label {}'.format(idx, label))

Data(edge_index=[2, 168], x=[37, 3], y=[1])
Graph with index 100 has label tensor([4])


## 第三題：Index為200的Graph的Edge數量為多少？（5分）
## Question 3: What is the number of Edges for the Graph with Index 200? (5 marks)

In [ ]:
def get_graph_num_edges(pyg_dataset, idx):
  ## 回傳Graph中的edge數量
  ## 注意：dataset為無向圖的情況下，你不能將edge計算兩次
  ## 不允許直接使用data.num_edges
  ## 你可能會用到edge_index，為COO格式的Graph Connectivity
  ## Return the number of edges in the Graph
  ## Note: If the dataset is an undirected graph, you shouldn't count the edges twice
  ## Direct use of data.num_edges is not allowed
  ## You may use edge_index for the COO format of Graph Connectivity

  num_edges = 0

  ############# CODE HERE #################
  unique_edges = set()
  edge_index = get_graph_class(pyg_dataset, idx).edge_index
  for i in range(edge_index.size(1)):
    src = edge_index[0, i].item()
    trg = edge_index[1, i].item()
    unique_edges.add((min(src, trg), max(src, trg)))
  num_edges = len(unique_edges)
  #########################################

  return num_edges

idx = 200
num_edges = get_graph_num_edges(pyg_dataset, idx)
print('Graph with index {} has {} edges'.format(idx, num_edges))

Graph with index 200 has 53 edges


# 2 Open Graph Benchmark (OGB)

OGB是一系列大型圖資料集，為圖機器學習提供基準。它的資料集可以用OGB Data Loader進行自動下載、處理、切分。

OGB is a series of large graph datasets that provide a benchmark for graph machine learning. Its datasets can be downloaded, processed and sliced automatically using the OGB Data Loader.


## Dataset and Data

OGB也支持PyG dataset和data，這邊我們以`ogbn-arxiv`為例。

OGB also supports PyG dataset and data, here we take `ogbn-arxiv` as an example



In [ ]:
import torch_geometric.transforms as T
from ogb.nodeproppred import PygNodePropPredDataset

dataset_name = 'ogbn-arxiv'
# Load the dataset and transform it to sparse tensor
dataset = PygNodePropPredDataset(name=dataset_name,
                                 transform=T.ToSparseTensor())
print('The {} dataset has {} graph'.format(dataset_name, len(dataset)))

# Extract the graph
data = dataset[0]
print(data)

Downloaded 0.08 GB: 100%|██████████| 81/81 [00:01<00:00, 77.00it/s]


Extracting dataset/arxiv.zip


Processing...


Loading necessary files...
This might take a while.
Processing graphs...


100%|██████████| 1/1 [00:00<00:00, 1882.54it/s]


Converting graphs into PyG objects...


100%|██████████| 1/1 [00:00<00:00, 2013.59it/s]

Saving...



Done!


The ogbn-arxiv dataset has 1 graph
Data(num_nodes=169343, x=[169343, 128], node_year=[169343, 1], y=[169343, 1], adj_t=[169343, 169343, nnz=1166243])


## 第四題：ogbn-arxiv的node的feature維度為多少？（5分）

## Question 4: What is the number of features of the node of ogbn-arxiv? （5 marks)

In [ ]:
def graph_num_features(data):
  # return feature number of the graph

  num_features = 0

  ############# CODE HERE #################
  num_features = data.num_features
  #########################################

  return num_features

num_features = graph_num_features(data)
print('The graph has {} features'.format(num_features))

The graph has 128 features


# 3 GNN: Node性質預測 GNN: Node Property Prediction

我們將使用Pytorch Geometric建構GCN，並將其用於node性質預測。GCN請參考這篇[論文](https://arxiv.org/pdf/1609.02907.pdf)

你不需要自己寫GCN的卷積層，可以直接用PyG建好的`GCNConv`層：https://pytorch-geometric.readthedocs.io/en/latest/modules/nn.html?highlight=GCNConv#torch_geometric.nn.conv.GCNConv

We will use Pytorch Geometric to build the GCN and use it for node property prediction. for the GCN see this [paper](https://arxiv.org/pdf/1609.02907.pdf)

You don't need to write your own GCN convolution layer, you can just use the `GCNConv` layer built by PyG: https://pytorch-geometric.readthedocs.io/en/latest/modules/nn.html?highlight=GCNConv#torch_geometric.nn.conv.GCNConv

In [ ]:
import torch
import torch.nn.functional as F
print(torch.__version__)

# The PyG built-in GCNConv
from torch_geometric.nn import GCNConv

import torch_geometric.transforms as T
from ogb.nodeproppred import PygNodePropPredDataset, Evaluator

1.13.1+cu117


## Load and Preprocess the Dataset

In [ ]:
dataset_name = 'ogbn-arxiv'
dataset = PygNodePropPredDataset(name=dataset_name,
                                 transform=T.ToSparseTensor())
data = dataset[0]

# Make the adjacency matrix to symmetric
data.adj_t = data.adj_t.to_symmetric()

device = 'cuda' if torch.cuda.is_available() else 'cpu'

# If you use GPU, the device should be cuda
print('Device: {}'.format(device))

data = data.to(device)
split_idx = dataset.get_idx_split()
train_idx = split_idx['train'].to(device)

Device: cuda


## GCN Model (10分)

實作GCN模型，請按照下圖所示的結構初始化所需要的layer，並實作`forwad`。BN為Batch Normalization。

Please follow the figure below to implement your `forward` function. BN is Batch


![test](https://drive.google.com/uc?id=128AuYAXNXGg7PIhJJ7e420DoPWKb-RtL)

In [ ]:
import torch.nn as nn
from torch.nn import BatchNorm1d
class GCN(torch.nn.Module):
    def __init__(self, input_dim, hidden_dim, output_dim, num_layers,
                 dropout, return_embeds=False):
        # 初始化self.convs, self.bns, and self.softmax. 請記得參考Pytorch文檔。
        # Initialize self.convs, self.bns, and self.softmax. please refer to Pytorch document
        # num_layers為GNN層數
        # num_layers is the number of GNN layer

        super(GCN, self).__init__()

        # A list of GCNConv layers，可以使用torch.nn.ModuleList，注意層數！
        # A list of GCNConv layers，you can use torch.nn.ModuleList, remind the number of layers！
        self.convs = None

        # A list of 1D batch normalization layers，可以使用torch.nn.ModuleList，注意層數！
        # A list of 1D batch normalization layers, you can use torch.nn.ModuleList, remind the number of layers！
        self.bns = None

        # The log softmax layer
        self.softmax = None

        ############# CODE HERE ############
        ## 1. GCNConv請參考：
        ## 1. GCNConv reference：
        ## https://pytorch-geometric.readthedocs.io/en/latest/modules/nn.html#torch_geometric.nn.conv.GCNConv
        ## 2. BatchNorm1d請參考：
        ## 2. BatchNorm1d reference：
        ## https://pytorch.org/docs/stable/generated/torch.nn.BatchNorm1d.html
        self.convs = nn.ModuleList([GCNConv(input_dim, hidden_dim)])
        self.bns = nn.ModuleList([BatchNorm1d(hidden_dim)])
        for _ in range(num_layers - 2):
            self.convs.append(GCNConv(hidden_dim, hidden_dim))
            self.bns.append(BatchNorm1d(hidden_dim))
        self.convs.append(GCNConv(hidden_dim, output_dim))
        self.softmax = nn.LogSoftmax(dim=1)
        #########################################

        # Probability of an element to be zeroed
        self.dropout = dropout

        # Skip classification layer and return node embeddings
        self.return_embeds = return_embeds

    def reset_parameters(self):
        for conv in self.convs:
            conv.reset_parameters()
        for bn in self.bns:
            bn.reset_parameters()

    def forward(self, x, adj_t):
        # 輸入x為node feature tensor，adj_t為edge index tensor，請回傳output tensor，計算過程參考上方圖片
        # Input x is node feature tensor，adj_t is edge index tensor，please return output tensor, calculation prcess can be refernce from the figure on top.

        out = None

        ############# CODE HERE ############
        ## 1. 請嚴格按照上圖說明進行神經網絡建構
        ## 2. 可以使用F.relu和F.dropout：https://pytorch.org/docs/stable/nn.functional.html
        ## 3. 請透過self.training設置F.dropout的使用時機（self.training==True時才進行dropout）
        ## 1. Please follow the above instructions strictly for the construction of the neural network
        ## 2. you can use F.relu and F.dropout: https://pytorch.org/docs/stable/nn.functional.html
        ## 3. Please set the use of F.dropout through self.training (dropout will be performed only when self.training==True)
        for i, conv in enumerate(self.convs[:-1]):
          x = F.dropout(F.relu(self.bns[i](conv(x, adj_t))), p=self.dropout, training=self.training)
        x = self.convs[-1](x, adj_t)
        out = self.softmax(x)
        #########################################

        return out

In [ ]:
def train(model, data, train_idx, optimizer, loss_fn):
    # 使用傳入的optimizer和loss_fn來訓練模型
    # Use the input optimizer and loss_fn to train the model
    # 此處不需使用batch概念
    # you don't need the concept of batch here
    model.train()
    loss = 0

    ############# CODE HERE ############
    ## 1. Optimizer梯度清零
    ## 2. 資料餵入模型
    ## 3. 用train_idx作為index來選擇output和label
    ## 4. 將選擇好的output和label都餵進loss_fn
    ## 1. Zero grad the optimizer
    ## 2. Feed the data into the model
    ## 3. Slicing the model output and label by train_idx
    ## 4. Feed the sliced output and label to loss_fn
    optimizer.zero_grad()
    data = data.to(device)
    output = model(data.x, data.adj_t)
    train_idx = train_idx.to(data.x.device)
    output = output[train_idx]
    labels = data.y[train_idx].squeeze()
    loss = loss_fn(output, labels)
    #########################################

    loss.backward()
    optimizer.step()

    return loss.item()

In [ ]:
# Test function
@torch.no_grad()
def test(model, data, split_idx, evaluator):
    # 使用split_idx和evaluator評估模型表現
    # please use split_idx adn evaluator to evaluate the model
    model.eval()

    # The output of model on all data
    out = None

    ############# CODE HERE ############
    ## 1. 完成out的運算即可，記得將輸入資料轉移至device上
    ## 1. Just get output using model and remember to transfer the input data to the device
    data = data.to(device)
    out = model(data.x, data.adj_t)
    #########################################

    y_pred = out.argmax(dim=-1, keepdim=True)

    train_acc = evaluator.eval({
        'y_true': data.y[split_idx['train']],
        'y_pred': y_pred[split_idx['train']],
    })['acc']
    valid_acc = evaluator.eval({
        'y_true': data.y[split_idx['valid']],
        'y_pred': y_pred[split_idx['valid']],
    })['acc']
    test_acc = evaluator.eval({
        'y_true': data.y[split_idx['test']],
        'y_pred': y_pred[split_idx['test']],
    })['acc']

    return train_acc, valid_acc, test_acc

In [ ]:
# 注意：請勿修改此處參數！
# Don't change!
args = {
    'device': device,
    'num_layers': 3,
    'hidden_dim': 256,
    'dropout': 0.5,
    'lr': 0.01,
    'epochs': 100,
}
args

{'device': 'cuda',
 'num_layers': 3,
 'hidden_dim': 256,
 'dropout': 0.5,
 'lr': 0.01,
 'epochs': 100}

In [ ]:
model = GCN(data.num_features, args['hidden_dim'],
            dataset.num_classes, args['num_layers'],
            args['dropout']).to(device)
evaluator = Evaluator(name='ogbn-arxiv')

In [ ]:
import copy

model.reset_parameters()

optimizer = torch.optim.Adam(model.parameters(), lr=args['lr'])
loss_fn = F.nll_loss

best_model = None
best_valid_acc = 0

for epoch in range(1, 1 + args["epochs"]):
  loss = train(model, data, train_idx, optimizer, loss_fn)
  result = test(model, data, split_idx, evaluator)
  train_acc, valid_acc, test_acc = result
  if valid_acc > best_valid_acc:
      best_valid_acc = valid_acc
      best_model = copy.deepcopy(model)
  print(f'Epoch: {epoch:02d}, '
        f'Loss: {loss:.4f}, '
        f'Train: {100 * train_acc:.2f}%, '
        f'Valid: {100 * valid_acc:.2f}% '
        f'Test: {100 * test_acc:.2f}%')

Epoch: 01, Loss: 4.2563, Train: 25.92%, Valid: 29.20% Test: 26.23%
Epoch: 02, Loss: 2.3646, Train: 25.39%, Valid: 22.47% Test: 27.25%
Epoch: 03, Loss: 1.9818, Train: 23.59%, Valid: 14.39% Test: 12.21%
Epoch: 04, Loss: 1.7963, Train: 27.21%, Valid: 15.41% Test: 12.38%
Epoch: 05, Loss: 1.7041, Train: 29.78%, Valid: 17.91% Test: 15.37%
Epoch: 06, Loss: 1.6201, Train: 28.80%, Valid: 17.73% Test: 15.32%
Epoch: 07, Loss: 1.5464, Train: 27.12%, Valid: 17.27% Test: 14.62%
Epoch: 08, Loss: 1.4926, Train: 25.96%, Valid: 16.96% Test: 14.56%
Epoch: 09, Loss: 1.4519, Train: 26.87%, Valid: 18.72% Test: 16.47%
Epoch: 10, Loss: 1.4021, Train: 28.26%, Valid: 21.93% Test: 20.16%
Epoch: 11, Loss: 1.3686, Train: 30.54%, Valid: 27.19% Test: 25.86%
Epoch: 12, Loss: 1.3402, Train: 33.07%, Valid: 32.53% Test: 32.77%
Epoch: 13, Loss: 1.3072, Train: 35.47%, Valid: 37.11% Test: 38.54%
Epoch: 14, Loss: 1.2874, Train: 37.89%, Valid: 40.21% Test: 41.95%
Epoch: 15, Loss: 1.2655, Train: 40.74%, Valid: 43.52% Test: 45

In [ ]:
best_result = test(best_model, data, split_idx, evaluator)
train_acc, valid_acc, test_acc = best_result
print(f'Best model: '
      f'Train: {100 * train_acc:.2f}%, '
      f'Valid: {100 * valid_acc:.2f}% '
      f'Test: {100 * test_acc:.2f}%')

Best model: Train: 73.55%, Valid: 71.91% Test: 70.93%


## 第五題：你的模型的`best_model`的validation和test accuracy（20分）
## Question 5: validation and test accuracy of your `best_model` (20 points)

此題不需填寫，保留log即可   
This question does not need to be filled in, just keep the log.

# 4 GNN: Graph性質預測
# 4 GNN: Graph classification
我們會建立一個圖神經網絡來預測圖性質（圖分類），ogbg-molhiv是一個分子結構資料集。

We will build a graph neural network to predict graph properties (graph classification). The ogbg-molhiv is a dataset of molecular structure.

## Load and preprocess the dataset

In [ ]:
from ogb.graphproppred import PygGraphPropPredDataset, Evaluator
from torch_geometric.data import DataLoader
from tqdm.notebook import tqdm

# Load the dataset
dataset = PygGraphPropPredDataset(name='ogbg-molhiv')

device = 'cuda' if torch.cuda.is_available() else 'cpu'
print('Device: {}'.format(device))

split_idx = dataset.get_idx_split()

# Check task type
print('Task type: {}'.format(dataset.task_type))

Downloaded 0.00 GB: 100%|██████████| 3/3 [00:00<00:00, 13.67it/s]
Processing...


Extracting dataset/hiv.zip
Loading necessary files...
This might take a while.
Processing graphs...


100%|██████████| 41127/41127 [00:00<00:00, 98470.39it/s] 


Converting graphs into PyG objects...


100%|██████████| 41127/41127 [00:01<00:00, 29355.26it/s]


Saving...
Device: cuda
Task type: binary classification


Done!


In [ ]:
# Load the data sets into dataloader
# 每個Batch 32張Graph，training需打亂順序
# We will train the graph classification task on a batch of 32 graphs
# Shuffle the order of graphs for training set
train_loader = DataLoader(dataset[split_idx["train"]], batch_size=32, shuffle=True, num_workers=0)
valid_loader = DataLoader(dataset[split_idx["valid"]], batch_size=32, shuffle=False, num_workers=0)
test_loader = DataLoader(dataset[split_idx["test"]], batch_size=32, shuffle=False, num_workers=0)

/usr/local/lib/python3.10/dist-packages/torch_geometric/deprecation.py:26: UserWarning: 'data.DataLoader' is deprecated, use 'loader.DataLoader' instead
  warnings.warn(out)


In [ ]:
# 注意，請勿改變此處參數！
# Don't change!
args = {
    'device': device,
    'num_layers': 5,
    'hidden_dim': 256,
    'dropout': 0.5,
    'lr': 0.001,
    'epochs': 30,
}
args

{'device': 'cuda',
 'num_layers': 5,
 'hidden_dim': 256,
 'dropout': 0.5,
 'lr': 0.001,
 'epochs': 30}

## Graph Prediction Model（15分）

接下來將實作GCN圖預測模型。其中我們會重用上面的GCN模型來生成`node_embeddings`，並在nodes之上使用Global Pooling得到圖embedding，來預測整張圖的性質/類別。

The next step is to implement the GCN graph prediction model. In this we will reuse the above GCN model to generate `node_embeddings`, and use Global Pooling on top of nodes to obtain graph embeddings to predict the nature/class of the whole graph.

In [ ]:
from ogb.graphproppred.mol_encoder import AtomEncoder
from torch_geometric.nn import global_add_pool, global_mean_pool

class GCN_Graph(torch.nn.Module):
    def __init__(self, hidden_dim, output_dim, num_layers, dropout):
        super(GCN_Graph, self).__init__()

        # Load encoders for Atoms in molecule graphs
        self.node_encoder = AtomEncoder(hidden_dim)

        # Node embedding model
        self.gnn_node = GCN(hidden_dim, hidden_dim,
            hidden_dim, num_layers, dropout, return_embeds=True)

        self.pool = None

        ############# CODE HERE ############
        ## 將self.pool初始化為global mean pooling layer
        ## Initialize self.pool to global mean pooling layer
        ## https://pytorch-geometric.readthedocs.io/en/latest/modules/nn.html#global-pooling-layers
        self.pool = global_mean_pool
        #########################################

        # Output layer
        self.linear = torch.nn.Linear(hidden_dim, output_dim)


    def reset_parameters(self):
      self.gnn_node.reset_parameters()
      self.linear.reset_parameters()

    def forward(self, batched_data):
        # 輸入為batched data，輸出為batched output tensor
        x, edge_index, batch = batched_data.x, batched_data.edge_index, batched_data.batch
        embed = self.node_encoder(x)

        out = None

        ############# CODE HERE ############
        ## 1. 使用GCN來建立node embeddings
        ## 2. 使用global pooling layer為全Graph建立Embedding（或representation）
        ## https://pytorch-geometric.readthedocs.io/en/latest/modules/nn.html#global-pooling-layers
        ## 3. 使用單層linear預測圖類別
        ## 1. Construct node embeddings using existing GCN model
        ## 2. Use global pooling layer to construct features for the whole graph
        ## https://pytorch-geometric.readthedocs.io/en/latest/modules/nn.html#global-pooling-layers
        ## 3. Use a linear layer to predict the graph property
        node_embeds = self.gnn_node(embed, edge_index)
        pooled = self.pool(node_embeds, batch)
        out = self.linear(pooled)
        #########################################

        return out

In [ ]:
def train(model, device, data_loader, optimizer, loss_fn):
    # 訓練模型
    # model training
    model.train()
    loss = 0

    for step, batch in enumerate(tqdm(data_loader, desc="Iteration")):
      batch = batch.to(device)

      if batch.x.shape[0] == 1 or batch.batch[-1] == 0:
          pass
      else:
        ## 計算training loss時，忽略nan（無標籤）： `nan == nan` is False
        ## ignore nan targets (unlabeled) when computing training loss.
        is_labeled = batch.y == batch.y

        ############# CODE HERE ############
        ## 1. 將optimizer中的梯度清零
        ## 2. 將data餵入模型
        ## 3. 使用is_labeled選取非nan的輸出和label
        ## 4. 記得將label改為float格式（提示：.float()）
        ## 5. 將output和label都送入loss_fn計算loss
        ## 1. Zero grad the optimizer
        ## 2. Feed the data into the model
        ## 3. Use `is_labeled` mask to filter output and labels
        ## 4. You might change the type of label
        ## 5. Feed the output and label to loss_fn
        optimizer.zero_grad()
        output = model(batch)
        is_labeled = ~torch.isnan(batch.y)
        output = output[is_labeled]
        labels = batch.y[is_labeled]
        labels = labels.float()
        loss = loss_fn(output, labels)
        #########################################

        loss.backward()
        optimizer.step()

    return loss.item()

In [ ]:
def eval(model, device, loader, evaluator):
    model.eval()
    y_true = []
    y_pred = []

    for step, batch in enumerate(tqdm(loader, desc="Iteration")):
        batch = batch.to(device)

        if batch.x.shape[0] == 1:
            pass
        else:
            with torch.no_grad():
                pred = model(batch)

            y_true.append(batch.y.view(pred.shape).detach().cpu())
            y_pred.append(pred.detach().cpu())

    y_true = torch.cat(y_true, dim = 0).numpy()
    y_pred = torch.cat(y_pred, dim = 0).numpy()

    input_dict = {"y_true": y_true, "y_pred": y_pred}

    return evaluator.eval(input_dict)

In [ ]:
model = GCN_Graph(args['hidden_dim'],
            dataset.num_tasks, args['num_layers'],
            args['dropout']).to(device)
evaluator = Evaluator(name='ogbg-molhiv')

In [ ]:
import copy

model.reset_parameters()

optimizer = torch.optim.Adam(model.parameters(), lr=args['lr'])
loss_fn = torch.nn.BCEWithLogitsLoss()

best_model = None
best_valid_acc = 0

for epoch in range(1, 1 + args["epochs"]):
  print('Training...')
  loss = train(model, device, train_loader, optimizer, loss_fn)

  print('Evaluating...')
  train_result = eval(model, device, train_loader, evaluator)
  val_result = eval(model, device, valid_loader, evaluator)
  test_result = eval(model, device, test_loader, evaluator)

  train_acc, valid_acc, test_acc = train_result[dataset.eval_metric], val_result[dataset.eval_metric], test_result[dataset.eval_metric]
  if valid_acc > best_valid_acc:
      best_valid_acc = valid_acc
      best_model = copy.deepcopy(model)
  print(f'Epoch: {epoch:02d}, '
        f'Loss: {loss:.4f}, '
        f'Train: {100 * train_acc:.2f}%, '
        f'Valid: {100 * valid_acc:.2f}% '
        f'Test: {100 * test_acc:.2f}%')

Training...


Iteration:   0%|          | 0/1029 [00:00<?, ?it/s]

Evaluating...


Iteration:   0%|          | 0/1029 [00:00<?, ?it/s]

Iteration:   0%|          | 0/129 [00:00<?, ?it/s]

...

Evaluating...


Iteration:   0%|          | 0/1029 [00:00<?, ?it/s]

Iteration:   0%|          | 0/129 [00:00<?, ?it/s]

Iteration:   0%|          | 0/129 [00:00<?, ?it/s]

Epoch: 30, Loss: 0.0480, Train: 83.74%, Valid: 77.79% Test: 75.89%


In [ ]:
train_acc = eval(best_model, device, train_loader, evaluator)[dataset.eval_metric]
valid_acc = eval(best_model, device, valid_loader, evaluator)[dataset.eval_metric]
test_acc = eval(best_model, device, test_loader, evaluator)[dataset.eval_metric]

print(f'Best model: '
      f'Train: {100 * train_acc:.2f}%, '
      f'Valid: {100 * valid_acc:.2f}% '
      f'Test: {100 * test_acc:.2f}%')

Iteration:   0%|          | 0/1029 [00:00<?, ?it/s]

Iteration:   0%|          | 0/129 [00:00<?, ?it/s]

Iteration:   0%|          | 0/129 [00:00<?, ?it/s]

Best model: Train: 83.09%, Valid: 81.41% Test: 73.52%


## 第六題：你的`best_model`的validation和test ROC-AUC分數（20分）
## Question 6: Validation and test ROC-AUC scores for your `best_model` (20 marks)

不需填寫，保留log即可  
No need to fill in, just keep the log above

## 第七題：請使用其他兩種PyG提供的global pooling layer進行實驗，比較它們與mean pooling的表現差別。（15分）

## Question 7: Please experiment with two other global pooling layers provided by PyG and compare their performance with that of mean pooling. (15 marks)

請不要改動上方的code，請在下面自己建新的程式碼區塊撰寫code並實驗。

Please do not change the code above, please create new code blocks below and experiment with it yourself.

Reference：https://pytorch-geometric.readthedocs.io/en/latest/modules/nn.html#global-pooling-layers

In [ ]:
## CODE HERE ##
# global_add_pool
from torch_geometric.nn import global_add_pool
class GCN_Graph(torch.nn.Module):
    def __init__(self, hidden_dim, output_dim, num_layers, dropout):
        super(GCN_Graph, self).__init__()

        # Load encoders for Atoms in molecule graphs
        self.node_encoder = AtomEncoder(hidden_dim)

        # Node embedding model
        self.gnn_node = GCN(hidden_dim, hidden_dim,
            hidden_dim, num_layers, dropout, return_embeds=True)

        self.pool = None

        ############# CODE HERE ############
        ## 將self.pool初始化為global mean pooling layer
        ## Initialize self.pool to global mean pooling layer
        ## https://pytorch-geometric.readthedocs.io/en/latest/modules/nn.html#global-pooling-layers
        self.pool = global_add_pool
        #########################################

        # Output layer
        self.linear = torch.nn.Linear(hidden_dim, output_dim)


    def reset_parameters(self):
      self.gnn_node.reset_parameters()
      self.linear.reset_parameters()

    def forward(self, batched_data):
        # 輸入為batched data，輸出為batched output tensor
        x, edge_index, batch = batched_data.x, batched_data.edge_index, batched_data.batch
        embed = self.node_encoder(x)

        out = None

        ############# CODE HERE ############
        ## 1. 使用GCN來建立node embeddings
        ## 2. 使用global pooling layer為全Graph建立Embedding（或representation）
        ## https://pytorch-geometric.readthedocs.io/en/latest/modules/nn.html#global-pooling-layers
        ## 3. 使用單層linear預測圖類別
        ## 1. Construct node embeddings using existing GCN model
        ## 2. Use global pooling layer to construct features for the whole graph
        ## https://pytorch-geometric.readthedocs.io/en/latest/modules/nn.html#global-pooling-layers
        ## 3. Use a linear layer to predict the graph property
        node_embeds = self.gnn_node(embed, edge_index)
        pooled = self.pool(node_embeds, batch)
        out = self.linear(pooled)
        #########################################

        return out

model = GCN_Graph(args['hidden_dim'],
            dataset.num_tasks, args['num_layers'],
            args['dropout']).to(device)
evaluator = Evaluator(name='ogbg-molhiv')

import copy

model.reset_parameters()

optimizer = torch.optim.Adam(model.parameters(), lr=args['lr'])
loss_fn = torch.nn.BCEWithLogitsLoss()

best_model = None
best_valid_acc = 0

for epoch in range(1, 1 + args["epochs"]):
  print('Training...')
  loss = train(model, device, train_loader, optimizer, loss_fn)

  print('Evaluating...')
  train_result = eval(model, device, train_loader, evaluator)
  val_result = eval(model, device, valid_loader, evaluator)
  test_result = eval(model, device, test_loader, evaluator)

  train_acc, valid_acc, test_acc = train_result[dataset.eval_metric], val_result[dataset.eval_metric], test_result[dataset.eval_metric]
  if valid_acc > best_valid_acc:
      best_valid_acc = valid_acc
      best_model = copy.deepcopy(model)
  print(f'Epoch: {epoch:02d}, '
        f'Loss: {loss:.4f}, '
        f'Train: {100 * train_acc:.2f}%, '
        f'Valid: {100 * valid_acc:.2f}% '
        f'Test: {100 * test_acc:.2f}%')

Training...


Iteration:   0%|          | 0/1029 [00:00<?, ?it/s]

Evaluating...


Iteration:   0%|          | 0/1029 [00:00<?, ?it/s]

Iteration:   0%|          | 0/129 [00:00<?, ?it/s]

...

Evaluating...


Iteration:   0%|          | 0/1029 [00:00<?, ?it/s]

Iteration:   0%|          | 0/129 [00:00<?, ?it/s]

Iteration:   0%|          | 0/129 [00:00<?, ?it/s]

Epoch: 30, Loss: 0.0049, Train: 77.91%, Valid: 76.52% Test: 71.88%


In [ ]:
train_acc = eval(best_model, device, train_loader, evaluator)[dataset.eval_metric]
valid_acc = eval(best_model, device, valid_loader, evaluator)[dataset.eval_metric]
test_acc = eval(best_model, device, test_loader, evaluator)[dataset.eval_metric]

print(f'Best model: '
      f'Train: {100 * train_acc:.2f}%, '
      f'Valid: {100 * valid_acc:.2f}% '
      f'Test: {100 * test_acc:.2f}%')

Iteration:   0%|          | 0/1029 [00:00<?, ?it/s]

Iteration:   0%|          | 0/129 [00:00<?, ?it/s]

Iteration:   0%|          | 0/129 [00:00<?, ?it/s]

Best model: Train: 78.53%, Valid: 76.73% Test: 71.53%


In [ ]:
## CODE HERE ##
# global_max_pool
from torch_geometric.nn import global_max_pool
class GCN_Graph(torch.nn.Module):
    def __init__(self, hidden_dim, output_dim, num_layers, dropout):
        super(GCN_Graph, self).__init__()

        # Load encoders for Atoms in molecule graphs
        self.node_encoder = AtomEncoder(hidden_dim)

        # Node embedding model
        self.gnn_node = GCN(hidden_dim, hidden_dim,
            hidden_dim, num_layers, dropout, return_embeds=True)

        self.pool = None

        ############# CODE HERE ############
        ## 將self.pool初始化為global mean pooling layer
        ## Initialize self.pool to global mean pooling layer
        ## https://pytorch-geometric.readthedocs.io/en/latest/modules/nn.html#global-pooling-layers
        self.pool = global_max_pool
        #########################################

        # Output layer
        self.linear = torch.nn.Linear(hidden_dim, output_dim)


    def reset_parameters(self):
      self.gnn_node.reset_parameters()
      self.linear.reset_parameters()

    def forward(self, batched_data):
        # 輸入為batched data，輸出為batched output tensor
        x, edge_index, batch = batched_data.x, batched_data.edge_index, batched_data.batch
        embed = self.node_encoder(x)

        out = None

        ############# CODE HERE ############
        ## 1. 使用GCN來建立node embeddings
        ## 2. 使用global pooling layer為全Graph建立Embedding（或representation）
        ## https://pytorch-geometric.readthedocs.io/en/latest/modules/nn.html#global-pooling-layers
        ## 3. 使用單層linear預測圖類別
        ## 1. Construct node embeddings using existing GCN model
        ## 2. Use global pooling layer to construct features for the whole graph
        ## https://pytorch-geometric.readthedocs.io/en/latest/modules/nn.html#global-pooling-layers
        ## 3. Use a linear layer to predict the graph property
        node_embeds = self.gnn_node(embed, edge_index)
        pooled = self.pool(node_embeds, batch)
        out = self.linear(pooled)
        #########################################

        return out

model = GCN_Graph(args['hidden_dim'],
            dataset.num_tasks, args['num_layers'],
            args['dropout']).to(device)
evaluator = Evaluator(name='ogbg-molhiv')

import copy

model.reset_parameters()

optimizer = torch.optim.Adam(model.parameters(), lr=args['lr'])
loss_fn = torch.nn.BCEWithLogitsLoss()

best_model = None
best_valid_acc = 0

for epoch in range(1, 1 + args["epochs"]):
  print('Training...')
  loss = train(model, device, train_loader, optimizer, loss_fn)

  print('Evaluating...')
  train_result = eval(model, device, train_loader, evaluator)
  val_result = eval(model, device, valid_loader, evaluator)
  test_result = eval(model, device, test_loader, evaluator)

  train_acc, valid_acc, test_acc = train_result[dataset.eval_metric], val_result[dataset.eval_metric], test_result[dataset.eval_metric]
  if valid_acc > best_valid_acc:
      best_valid_acc = valid_acc
      best_model = copy.deepcopy(model)
  print(f'Epoch: {epoch:02d}, '
        f'Loss: {loss:.4f}, '
        f'Train: {100 * train_acc:.2f}%, '
        f'Valid: {100 * valid_acc:.2f}% '
        f'Test: {100 * test_acc:.2f}%')

Training...


Iteration:   0%|          | 0/1029 [00:00<?, ?it/s]

Evaluating...


Iteration:   0%|          | 0/1029 [00:00<?, ?it/s]

Iteration:   0%|          | 0/129 [00:00<?, ?it/s]

...

Evaluating...


Iteration:   0%|          | 0/1029 [00:00<?, ?it/s]

Iteration:   0%|          | 0/129 [00:00<?, ?it/s]

Iteration:   0%|          | 0/129 [00:00<?, ?it/s]

Epoch: 30, Loss: 0.0078, Train: 85.47%, Valid: 80.06% Test: 76.67%


In [ ]:
train_acc = eval(best_model, device, train_loader, evaluator)[dataset.eval_metric]
valid_acc = eval(best_model, device, valid_loader, evaluator)[dataset.eval_metric]
test_acc = eval(best_model, device, test_loader, evaluator)[dataset.eval_metric]

print(f'Best model: '
      f'Train: {100 * train_acc:.2f}%, '
      f'Valid: {100 * valid_acc:.2f}% '
      f'Test: {100 * test_acc:.2f}%')

Iteration:   0%|          | 0/1029 [00:00<?, ?it/s]

Iteration:   0%|          | 0/129 [00:00<?, ?it/s]

Iteration:   0%|          | 0/129 [00:00<?, ?it/s]

Best model: Train: 83.51%, Valid: 80.17% Test: 74.99%


# 繳交 submition

點擊左上角檔案，下載為.ipynb格式，然後在eeclass中繳交該檔案即可。

clicking `File` and `Download .ipynb`. Upload the file to eeclass.